In [ ]:
import numpy as np
import pandas as pd
import geopandas as gpd

import holoviews as hv
import hvplot.pandas

from IPython import get_ipython

## 1. Data loading and wrangling

In [1]:
from matplotlib import pyplot as plt
import numpy as np
import pandas as pd
import geopandas as gpd
import os
import geoviews as gv
import geoviews.tile_sources as gvts
import hvplot.pandas
import holoviews as hv
import seaborn as sns
import altair as alt

np.random.seed(42)

palette5 = ["#61a262","#1a7328","#f2b4ae","#f26a4b","#f25d50"]
palette4 = ["#61a262","#1a7328","#f2b4ae","#f25d50"]
palette2 = ["#61a262","#f26a4b"]


### Load hospital reviews data with API 

Set up environment variable for kaggle API.

In [2]:
# set Kaggle key to environment variable
os.environ["KAGGLE_USERNAME"] = "lanxiao1120"
os.environ["KAGGLE_KEY"] = "dc6f594f7f5b866e3aec880f88948cb8"

# !!users need to install kaggle package first
from kaggle.api.kaggle_api_extended import KaggleApi
api = KaggleApi()
api.authenticate()

Load data from Kaggle with API.

In [3]:
#Signature: dataset_download_file(dataset, file_name, path=None, force=False, quiet=True)

# download file via API (has exceed limit)
"""
api.dataset_download_file('jiashenliu/515k-hotel-reviews-data-in-europe','Hotel_Reviews.csv', path='data')
"""
# read it
hotel_raw = pd.read_csv('data/Hotel_Reviews.csv.zip')

#hotel_raw.head()

### Wrangle data and join with country Boundaries

Transform data into geo data frame, transform date columns into date type, and trim data into those of 2016.

In [4]:
# set up coord
hotel = hotel_raw.copy()
hotel['geometry'] = gpd.points_from_xy(hotel['lng'], hotel['lat'])

# to geo df
hotel = gpd.GeoDataFrame(hotel, geometry="geometry", crs="EPSG:4326")

# convert crs to 3857
hotel = hotel.to_crs(epsg=3857)

# transform to date
hotel['Review_Date'] = pd.to_datetime(hotel['Review_Date'] ,format='%m/%d/%Y')

# trim into 2016
hotel = hotel.loc[hotel['Review_Date'] >= '2016-01-01']
hotel = hotel.loc[hotel['Review_Date'] < '2017-01-01']


In [5]:
%%opts WMTS [width=800, height=800, xaxis=None, yaxis=None]

hotel_2017 = hotel.loc[hotel['Review_Date']>'2017-01-01']

#hotel_2017.hvplot(geo=True, tiles=True, crs=3857)

Load data of European countries, and spatial join with hotel data.

In [6]:
# get country data 
url = 'https://gisco-services.ec.europa.eu/distribution/v2/countries/geojson/CNTR_RG_01M_2020_3857.geojson'
country = gpd.read_file(url)
#select col
country = country[['NAME_ENGL','geometry']]
# spatial join
hotel_joined = gpd.sjoin(hotel, country, op='within', how='left').drop(['index_right'], axis=1)


Change the name of the column for country.

In [7]:
# change column name
hotel_joined = hotel_joined.rename(
    columns={"NAME_ENGL": "Country"}
)


## 2. Exploratory analysis

##  3. Words frequency analysis & Interactive word clouds

What are the most commonly used words in hotel reviews? Analyzing it can help hotel owners understand the most valuable services that reviewers care about. 

So let's start with the comprehensive data. After removing the meaningless pause words, the four most common terms are in order: room, staff, location, and breakfast, which represent the four fields consumers care about most about hotel accommodation.

### Lower and split reviews

In [8]:
hotel_review = hotel_joined.copy()

hotel_review['Negative_Review'] = [review.lower().split() for review in hotel_review['Negative_Review']]
hotel_review['Positive_Review'] = [review.lower().split() for review in hotel_review['Positive_Review']]

### Remove stop words and punctuation

Load stop words and create a list.

In [9]:
import nltk
# download stop words
nltk.download('stopwords');

#Get the list of common stop words
stop_words = list(set(nltk.corpus.stopwords.words('english')))

[nltk_data] Downloading package stopwords to /Users/lexi/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Load common punctuation and create a list.

In [10]:
import string

punctuation = list(string.punctuation)

Remove stop words and punctuation from our reviews.

In [11]:
# list to remove
ignored = stop_words + punctuation

# Remove from each review column
hotel_review['Negative_Review'] = [[word for word in review if word not in ignored]
              for review in hotel_review['Negative_Review']]
hotel_review['Positive_Review'] = [[word for word in review if word not in ignored]
              for review in hotel_review['Positive_Review']]

### Count word frequencies first time

Create a new column containing both positive review and negative review.

In [12]:
hotel_review['Total_Review'] = pd.concat([hotel_review['Negative_Review'],hotel_review['Positive_Review']], 
                                         ignore_index=True)

hotel_review.head(n=2)

Hotel_Address  \
66   s Gravesandestraat 55 Oost 1092 AA Amsterdam ...   
67   s Gravesandestraat 55 Oost 1092 AA Amsterdam ...   

    Additional_Number_of_Scoring Review_Date  Average_Score   Hotel_Name  \
66                           194  2016-12-29            7.7  Hotel Arena   
67                           194  2016-12-28            7.7  Hotel Arena   

   Reviewer_Nationality                                    Negative_Review  \
66      United Kingdom   [asked, coffee, sugars, got, given, two, satch...   
67        South Africa   [room, cleaned, correctly, wine, champagne, gl...   

    Review_Total_Negative_Word_Counts  Total_Number_of_Reviews  \
66                                 40                     1403   
67                                 30                     1403   

                                      Positive_Review  \
66  [nice, open, room, bed, plenty, room, bath, ro...   
67  [begin, upgraded, made, wife, happy, room, spa...   

    Review_Total_Positive_Word_Counts  \
66                                 28   
67                                 92   

    Total_Number_of_Reviews_Reviewer_Has_Given  Reviewer_Score  \
66                                           7             9.2   
67                                           6             7.5   

                                                 Tags days_since_review  \
66  [' Leisure trip ', ' Couple ', ' Large King Ro...           217 day   
67  [' Leisure trip ', ' Couple ', ' Duplex Double...           218 day   

          lat       lng                        geometry      Country  \
66  52.360576  4.915968  POINT (547243.088 6865586.634)  Netherlands   
67  52.360576  4.915968  POINT (547243.088 6865586.634)  Netherlands   

                                         Total_Review  
66  [would, nice, one, responsible, cleaning, room...  
67  [first, impressions, dark, reception, made, us...

Define a helper function to calculate word frequencies from our data frame with other information.

In [13]:
def count_word(review_col, top=20):
    """
    Given a column of all words for every rhotel, count word frequencies across all reviews.
    
    By default, this returns the top 20 words, but you can specify a different value for `top`.
    """
    import itertools, collections
    
    # List of all words across hotels
    all_words = list(itertools.chain(*review_col))

    # Create counter
    counter = collections.Counter(all_words)
    
    return pd.DataFrame(counter.most_common(top),
                        columns=['words', 'count'])

In [14]:
counts_reviews = count_word(hotel_review['Total_Review'], top=20)

### Remove words that are not helpful

Remove words that are not very helpful for analysis.

In [15]:
neutral_words = ["nothing", "hotel", "would","could","one","bit","little","us","get","time","really","also","even"]
hotel_review['Total_Review'] = [[word for word in review if word not in neutral_words]
              for review in hotel_review['Total_Review']]

### Count words frequency for the final cleaned reviews

In [16]:
counts_reviews = count_word(hotel_review['Total_Review'], top=20)

Plot the words frequency result.

### Define functions to plot word clouds from word frequency

However, the focus does vary with the country and its tourism characteristics. So an interactive word cloud is made by the country and the largest number of words to show. 

As the results show, people are most concerned about the location and staff services in the Netherlands, Italy, Spain, and Austria, and there are more positive words in the evaluation (good, great, friendly, Etc.). In the UK, people are more concerned about rooms conditions and staff services, and the frequency of 'negative' is higher in reviews. In France, people pay more attention to rooms and breakfast, and negative words (negative, small, Etc.) appear more frequently. 

What's more, each country has its unique characteristics. For example, reviewers in France pay more attention to the night experience and shower experience.

In [17]:
import multidict as multidict
import numpy as np
import os
import re
from PIL import Image
from os import path
from wordcloud import WordCloud
import matplotlib.pyplot as plt
import itertools, collections


### Implement interactivity

Obtain a list of all countries.

In [18]:
list1 = list(hotel_review['Country'].unique())

# remove nan
list1 = list1[0:3]+list1[4:7]

Interact Functions.

## 4. Sentiment analysis

Are customers' reviews of each hotel positive or negative, subjective or objective? Let's analyze negative, positive, and integrated reviews.

### Create "text blobs" and pass text to

We create three text bolbs here, one for negative reviews, one for positive reviews, and one for total reviews.

In [19]:
import textblob

# concat positive and negative reviews together
hotel_review_raw = hotel_joined.copy()
hotel_review_raw['Total_Review'] = pd.concat([hotel_review_raw['Negative_Review'],hotel_review_raw['Positive_Review']], 
                                             ignore_index=True)

blobs_total = [textblob.TextBlob(review) for review in hotel_review_raw['Total_Review']]
blobs_neg = [textblob.TextBlob(review) for review in hotel_review_raw['Negative_Review']]
blobs_pos = [textblob.TextBlob(review) for review in hotel_review_raw['Positive_Review']]

### Combine all sentiment data into a DataFrame

In [20]:
hotel_sentiment = hotel_review_raw.copy()

hotel_sentiment['total_polarity'] = [blob.sentiment.polarity for blob in blobs_total]
hotel_sentiment['total_subjectivity'] = [blob.sentiment.subjectivity for blob in blobs_total]

hotel_sentiment['neg_polarity'] = [blob.sentiment.polarity for blob in blobs_neg]
hotel_sentiment['neg_subjectivity'] = [blob.sentiment.subjectivity for blob in blobs_neg]

hotel_sentiment['pos_polarity'] = [blob.sentiment.polarity for blob in blobs_pos]
hotel_sentiment['pos_subjectivity'] = [blob.sentiment.subjectivity for blob in blobs_pos]


### Explore the monthly trend of polarity

At last, explore the monthly trend of polarity and subjectivity. Interestingly, the reviewers' comments text will be more positive and subjective in the summer. This phenomenon may be because the weather and temperature will affect the users' mood or experience. In any case, it means that European hotels need to pay more attention to maintaining user experience, complaints, and evaluations in winter.

Sort the reviews in chronological order.

In [21]:
# sort 
hotel_sentiment = hotel_sentiment.sort_values(by='Review_Date', ascending=True)

# get month
import datetime as dt
hotel_sentiment['month'] = hotel_sentiment['Review_Date'].dt.month_name()


## 6. Clustering hotels based on DBSCAN

### Select and engineer features

In [53]:
feature_columns = [
    'Hotel_Name',
    'Average_Score', 
    'Total_Number_of_Reviews', 
    'total_subjectivity'
]

# select features
hotel_cluster = hotel_sentiment[feature_columns].copy()

# group by hotel and calculate mean
hotel_cluster = hotel_cluster.groupby('Hotel_Name').mean().reset_index().dropna()


### Normalize features

In [54]:
from sklearn.preprocessing import StandardScaler

# drop hotel name
hotel_scaled = hotel_cluster.drop(['Hotel_Name'], axis=1)

# Scale these features
scaler = StandardScaler()
hotel_scaled = scaler.fit_transform(hotel_scaled)


### Run DBSCAN to extract high-density clusters

In [55]:
from sklearn.cluster import dbscan 

# Run DBSCAN 
cores, labels = dbscan(hotel_scaled, eps=0.38, min_samples=30)

# Add the labels back to the original (unscaled) dataset
hotel_cluster['label'] = labels

# Extract the number of clusters 
num_clusters = hotel_cluster['label'].nunique() - 1


### Get mean statistics for clusters

In [56]:
# groupby by the label
grps = hotel_cluster.groupby('label')

# calculate average pickup hour and trip distance per cluster
avg_values = grps[[ 'Average_Score', 'Total_Number_of_Reviews', 'total_subjectivity']].mean().reset_index()


### Visualize the clusters

Join with other information that not involves clustering process. 

In [57]:
# merge with geometry
hotel_cluster = pd.merge(hotel_cluster, hotel_joined[['geometry','Hotel_Name','Country']],on=['Hotel_Name'], how='left').drop_duplicates()
hotel_cluster = gpd.GeoDataFrame(hotel_cluster, geometry="geometry", crs="EPSG:3857")

In [58]:
hotel_cluster.to_file("./data/hotel_cluster.geojson", driver='GeoJSON')


In [59]:
hotel_cluster = gpd.read_file("./data/hotel_cluster.geojson").to_crs(epsg=3857)

### Plot relation between scores, subjectivity, and number of reviews, coloring by  labels

Make plots interactive.

In [60]:
import panel as pn

pn.extension("vega")

import param as pm

class hotelsByCountry(pm.Parameterized):

    Countries = pm.ObjectSelector(default="United Kingdom", objects=["Netherlands", "United Kingdom", "France", "Spain", "Austria", "Italy"])

    
    @pm.depends("Countries")
    def scatter(self):
        """
        Return an altair scatter plot of the x and y by label.
        """
        df = hotel_cluster.loc[hotel_cluster['label']!=-1]
        df = df.loc[df['Country']==self.Countries]

        p1 = df.hvplot.scatter(x='Total_Number_of_Reviews', y='Average_Score', by='label', 
                               legend='right', height=300, width=400,
                               hover_cols=list(hotel_cluster.columns))
        
        return pn.Pane(p1, width=500)
    
    @pm.depends("Countries")
    def bar(self):
        df2 = hotel_cluster
        df2 = df2.loc[df2['Country']==self.Countries].groupby('label').mean()
        p2 = df2.hvplot.bar(y='total_subjectivity',by='label', height=300, legend='right')
        return pn.Pane(p2, width=400)
    
    def pointMap(self):
        df3 = hotel_cluster.loc[hotel_cluster['Country']==self.Countries]
        p3 = df3.hvplot(geo=True, tiles='CartoLight', coastline=True, hover_cols='all', crs=3857,)
        return pn.Pane(p3, width=900)

app = hotelsByCountry(name="")

Layout.

In [61]:
# The title
title = pn.Pane("<h3>Relationships within hotel clusters grouped by country</h3>", width=600,height=10)

# Layout the dashboard
panel = pn.Column(
    pn.Row(title),
    pn.Row(pn.Param(app.param, width=400,height=80)),
    pn.Row(app.scatter,app.bar),
    pn.Row(app.pointMap),
)

In [62]:
panel.servable()

Column
    [0] Row
        [0] Markdown(str, height=10, sizing_mode='fixed', width=600)
    [1] Row
        [0] Param(hotelsByCountry, height=80, sizing_mode='fixed', width=400)
    [2] Row
        [0] ParamMethod(method)
        [1] ParamMethod(method)
    [3] Row
        [0] ParamMethod(method)